## Imports

In [51]:
from geopy.geocoders import GoogleV3
from bs4 import BeautifulSoup
import requests
import time
import pandas as pd
import numpy as np
import urllib3
import re
from textwrap import shorten
import os
import geopandas as gpd

In [52]:
### Brokerage sale data
df = pd.read_csv('chicago_broker_rankings_august_2020_with_geo_points.csv')
### Geopandas read in for neighborhoods
chicago_neighborhoods = gpd.read_file('Boundaries - Neighborhoods.geojson')
### Geopandas read in for ZIP codes
chicago_zips = pd.read_csv('cook_zips_geo_data.csv')
chicago_zips = chicago_zips.filter(items=['Zip Code','geometry'],axis=1)
gs = gpd.GeoSeries.from_wkt(chicago_zips['geometry'])
geo_df = gpd.GeoDataFrame(chicago_zips, geometry=gs)

In [53]:
chicago_zips['Zip Code'] = chicago_zips['Zip Code'].astype(str)

In [54]:
chicago_zips.columns

Index(['Zip Code', 'geometry'], dtype='object')

In [55]:
chicago_neighborhoods

pri_neigh                           sec_neigh     shape_area  \
0         Grand Boulevard                         BRONZEVILLE  48492503.1554   
1            Printers Row                        PRINTERS ROW  2162137.97139   
2           United Center                       UNITED CENTER  32520512.7053   
3      Sheffield & DePaul                  SHEFFIELD & DEPAUL  10482592.2987   
4           Humboldt Park                       HUMBOLDT PARK  125010425.593   
5           Garfield Park                       GARFIELD PARK  89976069.5947   
6          North Lawndale                      NORTH LAWNDALE  89487422.0244   
7          Little Village                      LITTLE VILLAGE  127998297.819   
8           Armour Square             ARMOUR SQUARE,CHINATOWN  17141468.6356   
9             Avalon Park         AVALON PARK,CALUMET HEIGHTS  34852737.7366   
10               Burnside                    CHATHAM,BURNSIDE  16995983.2737   
11                Hermosa             BELMONT CRAIGIN,HERMOSA  32602059.4055   
12               Avondale                IRVING PARK,AVONDALE   55290595.482   
13           Logan Square                        LOGAN SQUARE  71256806.5518   
14        Calumet Heights         AVALON PARK,CALUMET HEIGHTS  48826241.5643   
15              East Side                      SOUTHEAST SIDE  83241728.0493   
16           West Pullman                        WEST PULLMAN  99365198.0822   
17         Garfield Ridge                      MIDWAY AIRPORT  117890778.429   
18               New City                   BACK OF THE YARDS  134636963.254   
19              Englewood                           ENGLEWOOD  173600015.009   
20         Grand Crossing         SOUTH SHORE, GRAND CROSSING  98853167.7093   
21                Ashburn                             ASHBURN  135460337.208   
22        Mount Greenwood         MOUNT GREENWOOD,MORGAN PARK  75584290.0209   
23            Morgan Park         MOUNT GREENWOOD,MORGAN PARK  91877340.6988   
24                 O'Hare                               OHARE  371835607.687   
25           Jackson Park                        JACKSON PARK  23545658.7772   
26                   Loop                                LOOP  31485185.0318   
27                Pullman                             PULLMAN   59001555.602   
28              Riverdale                           RIVERDALE  98389497.4143   
29              Hegewisch                      SOUTHEAST SIDE  145965741.437   
30              Greektown                           GREEKTOWN  1650645.84189   
31                Douglas                         BRONZEVILLE   46004621.137   
32          Museum Campus                       MUSEUM CAMPUS  15517071.1631   
33              Edgewater                           EDGEWATER  38865397.6718   
34              Lake View                           LAKE VIEW  76561177.2562   
35           Lincoln Park                        LINCOLN PARK  67401451.3717   
36       Magnificent Mile                       STREETERVILLE   882405.08616   
37         Lincoln Square                      LINCOLN SQUARE  71352328.2399   
38                Oakland                     OAKLAND,KENWOOD  16913961.0408   
39             Grant Park                          GRANT PARK  8974786.19635   
40              West Loop                           WEST LOOP  52945063.8967   
41            Fuller Park                   BACK OF THE YARDS  19916704.8692   
42          Andersonville                       ANDERSONVILLE  9584592.89906   
43               Woodlawn                            WOODLAWN   40515739.083   
44           Portage Park                        PORTAGE PARK  110196097.139   
45        Rush & Division                     RUSH & DIVISION   3489575.8016   
46      Little Italy, UIC                   LITTLE ITALY, UIC  71376244.1225   
47                Kenwood                     KENWOOD,OAKLAND  29071741.9283   
48            Rogers Park                         ROGERS PARK  51259902.4506   
49         Jeffe

## Correction Section

## HTML popup formatter

In [56]:
df.columns

Index(['Unnamed: 0', 'MLS#', 'Unique', 'Final Agent/Team', 'agent_type',
       'TRD Notes', 'PROPERTY TYPE', 'ADDRESS', 'CITY', 'STATE OR PROVINCE',
       'ZIP OR POSTAL CODE', 'SOLD DATE', 'PRICE', 'URL', 'full_address',
       'geo_address', 'loc', 'point', 'lat', 'lon', 'altitude'],
      dtype='object')

In [57]:
def popup_html(row):
    i = row
    address = df['full_address'].iloc[i]
    team = df['Final Agent/Team'].iloc[i]
    date_sold = df['SOLD DATE'].iloc[i]
    price = df['PRICE'].iloc[i]
    agent_type = df['agent_type'].iloc[i]
    
    html = '''<!DOCTYPE html>
    <html>
    <head>
    <h4>{}</h4>'''.format(address) + '''
    </head>
    <body>
    <strong>Team:</strong> {}'''.format(team) + '''<br> 
    <strong>Date sold:</strong> {}'''.format(date_sold) + '''<br>
    <strong>Price:</strong> {}'''.format(price) + '''<br>
    <strong>Type:</strong> {}'''.format(agent_type) + '''<br>
    </body>
    </html>
    '''
    return html


### HTML reservoir

In [58]:
#     Developer(s): <strong><em>{}'''.format(developer) + '''</strong></em><br><br>

## Map Maker

In [59]:
import folium
from folium.plugins import MarkerCluster
import branca

f = folium.Figure(width=750, height=750)
m = folium.Map(location=df[["lat", "lon"]].mean().to_list(),zoom_start=8)

title_html = '''
              <h4 align="center" style="font-size:16px"><b>{}</b></h4>
             '''.format(f'Top Chicago Broker Sales - August 2022')

# for _,r in chicago_neighborhoods.iterrows():
#     sim_geo = gpd.GeoSeries(r['geometry'])
#     geo_j = sim_geo.to_json()
#     geo_j = folium.GeoJson(data=geo_j,
#                            style_function=lambda x: {'fillColor': 'blue'})
#     folium.Popup(r['pri_neigh']).add_to(geo_j)
#     geo_j.add_to(m)

for _,r in geo_df.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                            style_function=lambda x: {'fillColor': 'blue'})
    folium.Popup(r['Zip Code']).add_to(geo_j)
    geo_j.add_to(m)

marker_cluster = MarkerCluster().add_to(m)

for i in range(0,len(df)):
    html = popup_html(i)
    iframe = branca.element.IFrame(html=html, width=510,height=280)
    popup = folium.Popup(folium.Html(html, script=True), max_width=510)
    folium.Marker([df['lat'].iloc[i],df['lon'].iloc[i]],
                 popup=popup).add_to(marker_cluster)

m.get_root().html.add_child(folium.Element(title_html))
m.fit_bounds(bounds=df[['lat','lon']].mean().to_list(),max_zoom=15)
# m.add_to(f)
m

In [60]:
m.save('index.html')

In [61]:
pd.set_option('display.max_rows',1000)

In [62]:
x = df.groupby(['ZIP OR POSTAL CODE'])['Final Agent/Team'].value_counts().groupby(level=0).nlargest(3)
x.to_csv('busiest_brokers_by_zip_code_chicago.csv')
x

ZIP OR POSTAL CODE  ZIP OR POSTAL CODE  Final Agent/Team                   
60601.0             60601.0             Leila Zammatta                         20
                                        The Laricy Team                         4
                                        Grigory Pekarsky                        3
60602.0             60602.0             Grigory Pekarsky                        3
                                        Bari & Elena Team                       1
                                        Kate Waddell Group                      1
60603.0             60603.0             The Laricy Team                         1
                                        Weinberg Choi Residential               1
60605.0             60605.0             The Laricy Team                        13
                                        NL Ferrata Team                         9
                                        Grigory Pekarsky                        6
60606.0             60

## Map URL snagger

Map template URL: `https://trd-digital.github.io/trd-news-interactive-maps/{map-folder-name}`

In [63]:
base_name = 'https://trd-digital.github.io/trd-news-interactive-maps/'

In [64]:
cwd = os.getcwd()

cwd = cwd.split('/')

final_name = base_name + cwd[-1]
print(final_name)

https://trd-digital.github.io/trd-news-interactive-maps/Chicago_broker_rankings_08_2022
